In [52]:
import openai
import pandas as pd
import time
import logging
import os
import glob
import multiprocessing as mp

In [2]:
news_data_raw = pd.read_csv('../data/master_articles.csv')

In [3]:
# Keep only news data 
columns_keep = ['Publishing Time', 'Ticker', 'Sector', 'Source', 'Headline', 'Text']
news_df = news_data_raw[columns_keep]

In [4]:
client = openai.OpenAI(
    api_key= #apikey,
    organization= #organization,
    project= #project
    ) 

### Example to see if API query is successful

In [5]:
completion = client.chat.completions.create(
    model="gpt-3.5-turbo",
    messages=[
        {"role": "system", "content": "You are a helpful assistant."},
        {"role": "user", "content": "Hello!"}
    ]
)

In [6]:
print(completion.choices[0].message)

ChatCompletionMessage(content='Hello! How can I assist you today?', role='assistant', function_call=None, tool_calls=None)


### Asking OpenAI to get sentiment

In [7]:
def get_sentiment(headline, summary):
    #prompt = f"Headline: {headline}\nSummary: {summary}\nSentiment: "
    prompt = (
        f"Headline: {headline}\n"
        f"Summary: {summary}\n"
        "Please provide the sentiment (positive, neutral, negative) and a sentiment score between -1 and 1."
    )
    try: 
        response = client.chat.completions.create(
            model = "gpt-4o-mini", #gpt-3.5-turbo
            messages=[
                {"role": "system", "content": "You are a helpful assistant."},
                {"role": "user", "content": prompt}
            ],
            max_tokens= 512, 
            temperature = 0.2 #from the API documentation, high values make the output random, while lower values make it more focused and deterministic 
        )

    except Exception as e:
        print(f"Error: {e}")
        return None
    
    return response

From the response, we get the message content (Positive, Neutral, Negative) and map it into (1, 0, -1)

In [8]:
response = get_sentiment(news_df["Headline"][0], news_df["Text"][0])

In [9]:
print(response)

ChatCompletion(id='chatcmpl-9rXl3czTPB1htOUlA16pimznEM3ln', choices=[Choice(finish_reason='stop', index=0, logprobs=None, message=ChatCompletionMessage(content='Sentiment: Negative  \nSentiment Score: -0.5', role='assistant', function_call=None, tool_calls=None))], created=1722548177, model='gpt-4o-mini-2024-07-18', object='chat.completion', service_tier=None, system_fingerprint='fp_0f03d4f0ee', usage=CompletionUsage(completion_tokens=13, prompt_tokens=84, total_tokens=97))


In [10]:
lines = response.choices[0].message.content.split('\n')
sentiment = " "
score = " "
for line in lines: 
    if "Sentiment: " in line:
        sentiment = line.split(": ")[1].strip().lower()
    elif "Sentiment Score: " in line:
        score = line.split(": ")[1]

print(sentiment, score)

negative -0.5


Input headline and summary text

In [11]:
print(news_df["Headline"][0])
print(news_df["Text"][0])

Did Wells Fargo CEO Tim Sloan Earn His $1 Million Raise?
We learned this week that the scandal-plagued bank's CEO received about 5.7% more in compensation in 2018.


What does our old finvader score say: 

finvader_tot = 0.2869

finvader_neg = 0.0

finvader_neu = 0.823

finvader_pos = 0.177. 

Which suggests that this article is neutral/slightly positive

But from openai we get a negative sentiment score.

In [12]:
news_data_raw.head(1)

Publishing Time Ticker   Sector           Source  \
0  2019-03-15 10:46:42+00:00    WFC  Finance  The Motley Fool   

                                            Headline  \
0  Did Wells Fargo CEO Tim Sloan Earn His $1 Mill...   

                                                Text  \
0  We learned this week that the scandal-plagued ...   

                                                 URL  finvader_tot  \
0  https://www.fool.com/investing/2019/03/14/did-...        0.2869   

   finvader_neg  finvader_neu  finvader_pos             Next Open Time  \
0           0.0         0.823         0.177  2019-03-15 13:30:00+00:00   

           Next Closing Time           Next Market Date  
0  2019-03-15 20:00:00+00:00  2019-03-18 04:00:00+00:00

### Improved function to get the sentiment and sentiment score

Sentiment = [Negative, Positive, Neutral] -> (-1, 1, 0)

Sentiment Score = [-1,1]

In [13]:
# Improved function
def get_sentiment_score(headline, summary, max_retries = 5, retry_delay = 5):
    #prompt = f"Headline: {headline}\nSummary: {summary}\nSentiment: "
    prompt = (
        f"Headline: {headline}\n"
        f"Summary: {summary}\n"
        "Please analyze the provided headline and summary and evaluate the sentiment expressed. Provide a sentiment (positive, neutral, negative) and a sentiment score between -1 and 1, with the score reflecting the strength of the sentiment and including up to three decimal places (e.g., -1.000 for extremely negative, 0.000 for neutral, 1.000 for extremely positive)."
        #"Please provide the sentiment (positive, neutral, negative) and a sentiment score between -1 and 1."
    )
    for attempt in range(max_retries):
        try: 
            response = client.chat.completions.create(
                model = "gpt-3.5-turbo", #gpt-4o-mini, gpt-3.5-turbo, gpt-4o-mini-2024-07-18
                messages=[
                    {"role": "system", "content": "You are a helpful assistant."},
                    {"role": "user", "content": prompt}
                ],
                max_tokens= 512, 
                temperature = 0.2 #from the API documentation, high values make the output random, while lower values make it more focused and deterministic 
            )

            lines = response.choices[0].message.content.split('\n')
            sentiment = None
            score = None
            for line in lines: 
                if "Sentiment: " in line:
                    sentiment = line.split(": ")[1].strip().lower()
                    if "positive" in sentiment:
                        sentiment = 1
                    elif "negative" in sentiment:
                        sentiment = -1 
                    else: 
                        sentiment = 0
                elif "Sentiment Score: " in line:
                    score = line.split(": ")[1]

            if sentiment is not None and score is not None:
                return sentiment, score

        except Exception as e:
            print(f"Attempt {attempt + 1} failed: {e}")
            time.sleep(retry_delay)
    
    return None, None

In [14]:
sentiment, score = get_sentiment_score(news_df["Headline"][0], news_df["Text"][0])

In [15]:
news_df_example = news_df.copy() #example

In [16]:
news_df_example.at[0, 'openai_sentiment'] = sentiment
news_df_example.at[0, 'openai_score'] = score

In [17]:
news_df_example.head(1)

Publishing Time Ticker   Sector           Source  \
0  2019-03-15 10:46:42+00:00    WFC  Finance  The Motley Fool   

                                            Headline  \
0  Did Wells Fargo CEO Tim Sloan Earn His $1 Mill...   

                                                Text  openai_sentiment  \
0  We learned this week that the scandal-plagued ...              -1.0   

  openai_score  
0       -0.500

### Another intermediate example 

In [18]:
news_df_5a = news_df.head(5)

In [19]:
news_df_5a

Publishing Time Ticker      Sector           Source  \
0  2019-03-15 10:46:42+00:00    WFC     Finance  The Motley Fool   
1  2019-03-15 10:47:26+00:00   AAPL  Technology  The Motley Fool   
2  2019-03-15 11:33:00+00:00     MA     Finance           Forbes   
3  2019-03-15 11:52:45+00:00    BAC     Finance         Benzinga   
4  2019-03-15 13:29:39+00:00  GOOGL  Technology         Benzinga   

                                            Headline  \
0  Did Wells Fargo CEO Tim Sloan Earn His $1 Mill...   
1        Don't Underestimate Apple's iPhone Business   
2    A Closer Look At Mastercard's Key Value Drivers   
3  Jim Cramer Gives His Opinion On Bank Of Americ...   
4  Uber And Waymo Seeking Outside Funding For Aut...   

                                                Text  
0  We learned this week that the scandal-plagued ...  
1  The segment is an invaluable asset to Apple's ...  
2  Mastercard has consistently beat street estima...  
3  On CNBC's "Mad Money Lightning Round", Jim Cra...  
4  Commercially viable autonomous vehicle (AV) te...

In [20]:
def apply_sentiment(row):
    sentiment, score = get_sentiment_score(row['Headline'], row['Text'])
    return pd.Series([sentiment, score])#sentiment, score #pd.Series([sentiment, score], index=['openai_sentiment', 'openai_score'])

In [21]:
results = news_df_5a.apply(apply_sentiment, axis = 1)

In [22]:
results

0       1
0 -1  -0.600
1  1   0.750
2  1   0.800
3  1   0.600
4  0   0.000

In [23]:
news_df_5a.loc[:, 'openai_sentiment'] = results[0]
news_df_5a.loc[:, 'openai_score'] = results[1]

/tmp/ipykernel_530370/527286052.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  news_df_5a.loc[:, 'openai_sentiment'] = results[0]
/tmp/ipykernel_530370/527286052.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  news_df_5a.loc[:, 'openai_score'] = results[1]


In [24]:
news_df_5a

Publishing Time Ticker      Sector           Source  \
0  2019-03-15 10:46:42+00:00    WFC     Finance  The Motley Fool   
1  2019-03-15 10:47:26+00:00   AAPL  Technology  The Motley Fool   
2  2019-03-15 11:33:00+00:00     MA     Finance           Forbes   
3  2019-03-15 11:52:45+00:00    BAC     Finance         Benzinga   
4  2019-03-15 13:29:39+00:00  GOOGL  Technology         Benzinga   

                                            Headline  \
0  Did Wells Fargo CEO Tim Sloan Earn His $1 Mill...   
1        Don't Underestimate Apple's iPhone Business   
2    A Closer Look At Mastercard's Key Value Drivers   
3  Jim Cramer Gives His Opinion On Bank Of Americ...   
4  Uber And Waymo Seeking Outside Funding For Aut...   

                                                Text  openai_sentiment  \
0  We learned this week that the scandal-plagued ...                -1   
1  The segment is an invaluable asset to Apple's ...                 1   
2  Mastercard has consistently beat street estima...                 1   
3  On CNBC's "Mad Money Lightning Round", Jim Cra...                 1   
4  Commercially viable autonomous vehicle (AV) te...                 0   

  openai_score  
0       -0.600  
1        0.750  
2        0.800  
3        0.600  
4        0.000

### Now do for the whole dataset 

In [25]:
len(news_df)

63703

In [28]:
# logging info
logging.basicConfig(filename='sentiment_processing_0801.log', level=logging.INFO,
                    format='%(asctime)s %(levelname)s:%(message)s')

In [29]:
news_df_100_ex2 = news_df.head(100)

In [30]:
news_df_100_ex2.loc[:, 'openai_sentiment'] = pd.NA
news_df_100_ex2.loc[:, 'openai_score'] = pd.NA

/tmp/ipykernel_530370/3717748893.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  news_df_100_ex2.loc[:, 'openai_sentiment'] = pd.NA
/tmp/ipykernel_530370/3717748893.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  news_df_100_ex2.loc[:, 'openai_score'] = pd.NA


In [31]:
def process_batch(batch_df, batch_number): #, batch_size
    #results = []
    for local_index, row in batch_df.iterrows():
        global_index = row.name
        try:
            sentiment, score = get_sentiment_score(row['Headline'], row['Text'])

            #directly update
            news_df_100_ex2.at[global_index, "openai_sentiment"] = sentiment
            news_df_100_ex2.at[global_index, "openai_score"] = score

            logging.info(f"Processed row {global_index} successfully.")
            #results.append((local_index, sentiment, score))
            #logging.info(f"Processed row {batch_number * batch_size + local_index} successfully.")
        except Exception as e:
            logging.error(f"Error processing row {global_index}: {e}")
            #logging.error(f"Error processing row {batch_number * batch_size + local_index}: {e}")
    
    #batch_df.to_csv(f'processed_batch_{batch_number}.csv', index=False)
    
    #result_df = pd.DataFrame(results, columns = ['local_index', 'openai_sentiment', 'openai_score'])
    #result_df.to_csv(f'processed_batch_{batch_number}.csv', index=False)


In [32]:
len(news_df_100_ex2)

100

In [33]:
batch_size = 10
num_batches = len(news_df_100_ex2) // batch_size + 1

In [34]:
num_batches

11

In [96]:
for i in range(num_batches):
    start_idx = i * batch_size
    end_idx = min((i + 1) * batch_size, len(news_df_100_ex2))
    batch_df = news_df_100_ex2.iloc[start_idx:end_idx].copy()

    print(f"Processing batch {i+1}/{num_batches} (rows {start_idx} to {end_idx})")
    logging.info(f"Processing batch {i+1}/{num_batches} (rows {start_idx} to {end_idx})")
    process_batch(batch_df, i) #batch_size

try: 
    news_df_100_ex2.to_csv("processed_news_df_100_ex_refined3.csv", index=False)
    logging.info("Final DataFrame saved successfully.")
except Exception as e:
    logging.error(f"Error saving final DataFrame: {e}")

Processing batch 1/11 (rows 0 to 10)


Processing batch 2/11 (rows 10 to 20)
Processing batch 3/11 (rows 20 to 30)
Processing batch 4/11 (rows 30 to 40)
Processing batch 5/11 (rows 40 to 50)
Processing batch 6/11 (rows 50 to 60)
Processing batch 7/11 (rows 60 to 70)
Processing batch 8/11 (rows 70 to 80)
Processing batch 9/11 (rows 80 to 90)
Processing batch 10/11 (rows 90 to 100)
Processing batch 11/11 (rows 100 to 100)


Do an alternative using multiprocessing

In [72]:
def process_batch_mp(batch_info):
    batch_df, batch_number = batch_info
    results = []
    for local_index, row in batch_df.iterrows():
        global_index = row.name
        try: 
            sentiment, score = get_sentiment_score(row['Headline'], row['Text'])
            results.append((global_index, sentiment, score))
            logging.info(f"Processed row {global_index} successfully in batch {batch_number}.")
        except Exception as e:
            logging.error(f"Error processing row {global_index} in batch {batch_number}: {e}")
    return results

In [56]:
news_df_100_ex3 = news_df.head(100)
batch_size = 10
num_batches = len(news_df_100_ex3) // batch_size + 1

In [73]:
def update_dataframe(results, news_df):
    for global_index, sentiment, score in results:
        news_df.at[global_index, "openai_sentiment"] = sentiment
        news_df.at[global_index, "openai_score"] = score

In [59]:
batches = [(news_df_100_ex3.iloc[i * batch_size: (i + 1) * batch_size].copy(), i) for i in range(num_batches)]

In [62]:
if __name__ == "__main__":
    with mp.Pool(mp.cpu_count()) as pool:
        all_results = pool.map(process_batch_mp, batches)

    all_results_flat = [item for sublist in all_results for item in sublist]
    update_dataframe(all_results_flat, news_df_100_ex3)

    try: 
        news_df_100_ex3.to_csv("processed_news_df_100_MP.csv", index=False)
        logging.info("Final DataFrame saved successfully.")
    except Exception as e:
        logging.error(f"Error saving final DataFrame: {e}")

/tmp/ipykernel_530370/2497395941.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  news_df.at[global_index, "openai_sentiment"] = sentiment
/tmp/ipykernel_530370/2497395941.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  news_df.at[global_index, "openai_score"] = score


In [75]:
last_file = '/atlas/data19/guhitj/Erdos_DL/Erdos-2024-DL-Newsworthy/sentiment_analysis/news_split_csvs/news_df_chunk_638.csv'
df_last_file = pd.read_csv(last_file)

In [76]:
df_last_file

Publishing Time Ticker      Sector            Source  \
0  2024-03-15 21:03:01+00:00   AAPL  Technology  Business Insider   
1  2024-03-15 22:18:35+00:00   AAPL  Technology      The Guardian   
2  2024-03-15 23:21:00+00:00   AAPL  Technology      Market Watch   

                                            Headline  \
0  Tim Cook's comments about iPhone sales in Chin...   
1  Apple to pay $490m to settle claims it misled ...   
2  Apple to pay $490 million to settle claims it ...   

                                                Text  
0  Apple has agreed to pay $490 million to settle...  
1  Company denied that Tim Cook deceived investor...  
2  Apple Inc. has agreed to pay $490 million to s...

In [77]:
batch_size = 1
num_batches = len(df_last_file) // batch_size + 1

In [78]:
batches = [(df_last_file.iloc[i * batch_size: (i + 1) * batch_size].copy(), i) for i in range(num_batches)]

In [79]:
if __name__ == "__main__":
    with mp.Pool(mp.cpu_count()) as pool:
        all_results = pool.map(process_batch_mp, batches)

    all_results_flat = [item for sublist in all_results for item in sublist]
    update_dataframe(all_results_flat, df_last_file)

    try: 
        df_last_file.to_csv("results_news_splits/news_openai_sentiment_partial_638.csv", index=False)
        logging.info("Final DataFrame saved successfully.")
    except Exception as e:
        logging.error(f"Error saving final DataFrame: {e}")

In [92]:
file_99 = '/atlas/data19/guhitj/Erdos_DL/Erdos-2024-DL-Newsworthy/sentiment_analysis/news_split_csvs/news_df_chunk_99.csv'
df_file_99 = pd.read_csv(file_99)

In [93]:
len(df_file_99)

100

In [88]:
batch_size = 10
num_batches = len(df_file_99) // batch_size + 1
batches = [(df_file_99.iloc[i * batch_size: (i + 1) * batch_size].copy(), i) for i in range(num_batches)]

In [94]:
if __name__ == "__main__":
    with mp.Pool(mp.cpu_count()) as pool:
        all_results = pool.map(process_batch_mp, batches)

    all_results_flat = [item for sublist in all_results for item in sublist]
    update_dataframe(all_results_flat, df_file_99)

    try: 
        df_file_99.to_csv("results_news_splits/news_openai_sentiment_file99_new.csv", index=False)
        logging.info("Final DataFrame saved successfully.")
    except Exception as e:
        logging.error(f"Error saving final DataFrame: {e}")

Now for the whole dataset 

In [ ]:
# use the dataset i split in 100 each 
# loop over them , access them using glob 
# then set batch_size = 10


In [ ]:
# process_batch_mp function should be the same 

In [70]:
input_dir = 'news_split_csvs'
csv_files = sorted(glob.glob(os.path.join(input_dir, '*.csv')))
total_files = len(csv_files)

In [71]:
output_dir = 'results_news_splits'
os.makedirs(output_dir, exist_ok=True)

In [74]:
if __name__ == "__main__":
    for file_num, csv_file in enumerate(csv_files, start=1):
        # load csv splits
        batch_df = pd.read_csv(csv_file)

        # check if its last file, because the last file has 3 entries 
        is_last_file = (file_num == total_files)

        if is_last_file:
            print(f"Processing the last file {file_num}/{total_files} with batch_size = 1")
            for index, row in batch_df.iterrows():
                batch_df_single = batch_df.iloc[[index]]
                batches_full = [(batch_df_single, file_num)]

            with mp.Pool(mp.cpu_count()) as pool:
                all_results_flat = pool.map(process_batch_mp, batches_full)

            all_results_flat = [item for sublist in all_results for item in sublist]
            update_dataframe(all_results_flat, batch_df_single)

            # Save batch
            partial_filename = os.path.join(output_dir, f"news_openai_sentiment_partial_{file_num}_{index+1}.csv")
            batch_df_single.to_csv(partial_filename, index=False)

        else:
            print(f"Processing file {file_num}/{total_files}: {csv_file} with batch_size = 10")
            batch_size = 10
            num_batches = (len(batch_df) // batch_size) + (1 if len(batch_df) % batch_size != 0 else 0)
            for i in range(num_batches):
                start_idx = i * batch_size
                end_idx = min((i + 1) * batch_size, len(batch_df))
                batch_df_part = batch_df.iloc[start_idx:end_idx]
                batches_full = [(batch_df_part, i)]

                with mp.Pool(mp.cpu_count()) as pool:
                    all_results = pool.map(process_batch_mp, batches_full)

                all_results_flat = [item for sublist in all_results for item in sublist]
                update_dataframe(all_results_flat, batch_df_part)

                # Save updated batch_df_part immediately
                partial_filename = os.path.join(output_dir, f"news_openai_sentiment_partial_{file_num}_{i+1}.csv")
                batch_df_part.to_csv(partial_filename, index=False)
        
        if file_num < total_files:
            print(f"Sleeping for 3 minutes before processing the next file.")
            time.sleep(3 * 60)

Processing file 1/638: news_split_csvs/news_df_chunk_1.csv with batch_size = 10


/tmp/ipykernel_530370/2497395941.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  news_df.at[global_index, "openai_sentiment"] = sentiment
/tmp/ipykernel_530370/2497395941.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  news_df.at[global_index, "openai_score"] = score
/tmp/ipykernel_530370/2497395941.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pa

Sleeping for 3 minutes before processing the next file.
Processing file 2/638: news_split_csvs/news_df_chunk_10.csv with batch_size = 10


/tmp/ipykernel_530370/2497395941.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  news_df.at[global_index, "openai_sentiment"] = sentiment
/tmp/ipykernel_530370/2497395941.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  news_df.at[global_index, "openai_score"] = score
/tmp/ipykernel_530370/2497395941.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pa

Sleeping for 3 minutes before processing the next file.
Processing file 3/638: news_split_csvs/news_df_chunk_100.csv with batch_size = 10


...

/tmp/ipykernel_530370/2497395941.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  news_df.at[global_index, "openai_sentiment"] = sentiment
/tmp/ipykernel_530370/2497395941.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  news_df.at[global_index, "openai_score"] = score
/tmp/ipykernel_530370/2497395941.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pa

Sleeping for 3 minutes before processing the next file.
Processing file 637/638: news_split_csvs/news_df_chunk_98.csv with batch_size = 10


/tmp/ipykernel_530370/2497395941.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  news_df.at[global_index, "openai_sentiment"] = sentiment
/tmp/ipykernel_530370/2497395941.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  news_df.at[global_index, "openai_score"] = score
/tmp/ipykernel_530370/2497395941.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pa

Sleeping for 3 minutes before processing the next file.
Processing the last file 638/638 with batch_size = 1


/tmp/ipykernel_530370/2497395941.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  news_df.at[global_index, "openai_sentiment"] = sentiment


I split the files here, but it was done earlier in the jupyter notebook, i made a couple of edits and it ended up here. wont make any changes for now

In [95]:
news_df_full = news_df.copy()

In [39]:

output_dir = 'news_split_csvs'
os.makedirs(output_dir, exist_ok=True)

chunk_size = 100

In [40]:
for i in range(0, len(news_df_full), chunk_size):
    chunk_df = news_df_full.iloc[i:i + chunk_size]
    chunk_filename = f"{output_dir}/news_df_chunk_{i // chunk_size + 1}.csv"
    chunk_df.to_csv(chunk_filename, index=False)
    print(f"Saved {chunk_filename}, with {len(chunk_df)} rows")

Saved news_split_csvs/news_df_chunk_1.csv, with 100 rows
Saved news_split_csvs/news_df_chunk_2.csv, with 100 rows
Saved news_split_csvs/news_df_chunk_3.csv, with 100 rows
Saved news_split_csvs/news_df_chunk_4.csv, with 100 rows
Saved news_split_csvs/news_df_chunk_5.csv, with 100 rows
Saved news_split_csvs/news_df_chunk_6.csv, with 100 rows
Saved news_split_csvs/news_df_chunk_7.csv, with 100 rows
Saved news_split_csvs/news_df_chunk_8.csv, with 100 rows
Saved news_split_csvs/news_df_chunk_9.csv, with 100 rows
Saved news_split_csvs/news_df_chunk_10.csv, with 100 rows
Saved news_split_csvs/news_df_chunk_11.csv, with 100 rows
Saved news_split_csvs/news_df_chunk_12.csv, with 100 rows
Saved news_split_csvs/news_df_chunk_13.csv, with 100 rows
Saved news_split_csvs/news_df_chunk_14.csv, with 100 rows
Saved news_split_csvs/news_df_chunk_15.csv, with 100 rows
Saved news_split_csvs/news_df_chunk_16.csv, with 100 rows
Saved news_split_csvs/news_df_chunk_17.csv, with 100 rows
Saved news_split_csvs/n